# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with `YOUR IMPORT TEXT HERE`

In [2]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint

In [ ]:
# command used in terminal to import establishments.json into database 'uk_food' :

# mongoimport --type json -d uk_food -c establishments --drop --jsonArray Resources/establishments.json

# file successfully imported

In [3]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [4]:
# List all databases in MongoDB
database_names = mongo.list_database_names()

# Loop through the database names and print each one
for db_name in database_names:
    print(db_name)
    

admin
classDB
config
epa
fruits_db
local
met
petsitly_marketing
uk_food


In [5]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [6]:
# review the collections in our new database
collection_names = db.list_collection_names()

# explicit print
print(collection_names)

['establishments']


In [9]:
# review a document in the establishments collection

# assign to variable
document = db['establishments'].find_one()

# display
pprint(document)

{'AddressLine1': 'St Marys Church Of England Primary School',
 'AddressLine2': 'Warren Road',
 'AddressLine3': 'Folkestone',
 'AddressLine4': 'Kent',
 'BusinessName': 'St Marys COE (aided) Primary School',
 'BusinessType': 'School/college/university',
 'BusinessTypeID': 7845,
 'ChangesByServerID': 0,
 'Distance': 4591.871474174837,
 'FHRSID': 289353,
 'LocalAuthorityBusinessID': 'PI/000002468',
 'LocalAuthorityCode': '188',
 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk',
 'LocalAuthorityName': 'Folkestone and Hythe',
 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT19 6QH',
 'RatingDate': '2016-09-13T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': 5,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('6636638deb191ce7dc138a47'),
 'geocode': {'latitude': 51.085797, 'longitude': 1.194762},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/289353',
            '

In [8]:
# assign the collection to a variable
establishments = db['establishments']

In [10]:
# Added Cell
# Count the number of documents in the collection
num_documents = establishments.count_documents({})
print(f"Number of documents in the collection: {num_documents}")

Number of documents in the collection: 39779


## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [11]:
# Create a dictionary for the new restaurant data
restaurant_data = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}


In [12]:
# Insert New Restaurant into the collection 
result = establishments.insert_one(restaurant_data)

In [13]:
# Check that the new restaurant was inserted
print("Inserted document ID:", result.inserted_id)

Inserted document ID: 663663acf3210a7b5eed69b6


2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [14]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields

# set up query
query = {
    "BusinessType": "Restaurant/Cafe/Canteen"
}

# projection to include only BusinessTypeID and BusinessType fields
projection = {
    "_id": 0,  # Exclude the _id field
    "BusinessTypeID": 1,
    "BusinessType": 1
}

# Perform query
result = establishments.find_one(query, projection)

# Print the result
print(result)

{'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': 1}


3. Update the new restaurant with the `BusinessTypeID` you found.

In [15]:
# update the new restaurant with the correct BusinessTypeID - which is "1"

# Define the filter to find the document for "Penang Flavours"
filter = { "BusinessName": "Penang Flavours" }

# Define the update to set the correct BusinessTypeID
update = { "$set": { "BusinessTypeID": "1" } }

# Update the document for "Penang Flavours" with the correct BusinessTypeID
result = db.establishments.update_one(filter, update)

# Print the updated document
print(result.modified_count)


1


In [16]:
# Confirm that the new restaurant was updated

# Query to find the document for "Penang Flavours" restaurant
query = {'BusinessName': 'Penang Flavours'}
result = establishments.find_one(query)

# Check if the BusinessTypeID field matches the correct value
if result is not None:
    retrieved_business_type_id = result.get('BusinessTypeID')
    print(f"Retrieved BusinessTypeID: {retrieved_business_type_id}")
else:
    print("Restaurant 'Penang Flavours' not found in the database.")


Retrieved BusinessTypeID: 1


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [17]:
# Find how many documents have LocalAuthorityName as "Dover"
dover_count = establishments.count_documents({"LocalAuthorityName": "Dover"})

# display number found
print("Number of documents with LocalAuthorityName as 'Dover':", dover_count)



Number of documents with LocalAuthorityName as 'Dover': 994


In [18]:
# Delete all documents where LocalAuthorityName is "Dover"
result = establishments.delete_many({"LocalAuthorityName": "Dover"})

# display results
print("Number of documents deleted:", result.deleted_count)

Number of documents deleted: 994


In [19]:
# check if any remaining documents include Dover
dover_count = establishments.count_documents({"LocalAuthorityName": "Dover"})

# display number found (or hopefully not found...)
print("Number of documents with LocalAuthorityName as 'Dover':", dover_count)

Number of documents with LocalAuthorityName as 'Dover': 0


In [20]:
# check that other documents remain with 'find_one'
remaining_document = establishments.find_one()

print("One example of a remaining document in the collection:")
print(remaining_document)

One example of a remaining document in the collection:
{'_id': ObjectId('6636638deb191ce7dc138a47'), 'FHRSID': 289353, 'ChangesByServerID': 0, 'LocalAuthorityBusinessID': 'PI/000002468', 'BusinessName': 'St Marys COE (aided) Primary School', 'BusinessType': 'School/college/university', 'BusinessTypeID': 7845, 'AddressLine1': 'St Marys Church Of England Primary School', 'AddressLine2': 'Warren Road', 'AddressLine3': 'Folkestone', 'AddressLine4': 'Kent', 'PostCode': 'CT19 6QH', 'Phone': '', 'RatingValue': '5', 'RatingKey': 'fhrs_5_en-gb', 'RatingDate': '2016-09-13T00:00:00', 'LocalAuthorityCode': '188', 'LocalAuthorityName': 'Folkestone and Hythe', 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk', 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk', 'scores': {'Hygiene': 0, 'Structural': 0, 'ConfidenceInManagement': 0}, 'SchemeType': 'FHRS', 'geocode': {'longitude': '1.194762', 'latitude': '51.085797'}, 'RightToReply': '', 'Distance': 4591.871474174837, 'NewRati

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [21]:
# change data type from string to decimal for long and lat
establishments.update_many({}, [
    {"$set": {"geocode.longitude": {"$toDouble": "$geocode.longitude"}}},
    {"$set": {"geocode.latitude": {"$toDouble": "$geocode.latitude"}}}
])

UpdateResult({'n': 38786, 'nModified': 38786, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

Use `update_many` to convert `RatingValue` to integer numbers.

In [22]:
# Added Cell- count ratingvalue

# aggregate to count occurrences of each RatingValue
pipeline = [
    {"$group": {"_id": "$RatingValue", "count": {"$sum": 1}}},
    {"$sort": {"_id": 1}}  # Sort by RatingValue
]

result = list(establishments.aggregate(pipeline))

# print count of each unique RatingValue
for doc in result:
    print(f"RatingValue: {doc['_id']}, Count: {doc['count']}")

RatingValue: None, Count: 1
RatingValue: 0, Count: 65
RatingValue: 1, Count: 570
RatingValue: 2, Count: 533
RatingValue: 3, Count: 2269
RatingValue: 4, Count: 5441
RatingValue: 5, Count: 25816
RatingValue: Awaiting Inspection, Count: 42
RatingValue: AwaitingInspection, Count: 2069
RatingValue: AwaitingPublication, Count: 4
RatingValue: Exempt, Count: 1883
RatingValue: Pass, Count: 93


In [26]:
# set non 1-5 RatingValues to null
non_numeric_values = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt", None]
establishments.update_many({"RatingValue": {"$in": non_numeric_values}}, {'$set': {"RatingValue": 0}})


UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [27]:
# Added Cell- count ratingvalue

# aggregate to count occurrences of each RatingValue
pipeline = [
    {"$group": {"_id": "$RatingValue", "count": {"$sum": 1}}},
    {"$sort": {"_id": 1}}  # Sort by RatingValue
]

result = list(establishments.aggregate(pipeline))

# print count of each unique RatingValue
for doc in result:
    print(f"RatingValue: {doc['_id']}, Count: {doc['count']}")

RatingValue: 0, Count: 4092
RatingValue: 0, Count: 65
RatingValue: 1, Count: 570
RatingValue: 2, Count: 533
RatingValue: 3, Count: 2269
RatingValue: 4, Count: 5441
RatingValue: 5, Count: 25816


In [28]:
# change data type from string to integer for RatingValue
establishments.update_many({}, [
    {'$set': {'RatingValue': {'$toInt': '$RatingValue'}}}
])

print("Data type of RatingValue field changed to integer for all documents.")




Data type of RatingValue field changed to integer for all documents.


In [29]:
# check that coordinates and rating value are now numbers

for doc in establishments.find():
    latitude = doc.get('geocode', {}).get('latitude')
    longitude = doc.get('geocode', {}).get('longitude')
    rating_value = doc.get('RatingValue')

    print(f"Latitude Data Type: {type(latitude)}")
    print(f"Longitude Data Type: {type(longitude)}")
    print(f"Longitude Data Type: {type(rating_value)}")




Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class 'float'>
Longitude Data Type: <class 'float'>
Longitude Data Type: <class 'int'>
Latitude Data Type: <class '